## **Figure 3**: Effect of Spatial Resolution on Noise in SWMMIN Simulations

#### Importing required libraries

In [1]:
import pyswmm                   # Library for working with SWMM (Storm Water Management Model)
import pandas as pd             # Data manipulation and analysis library
import numpy as np              
import pathlib                  # Object-oriented filesystem paths
import matplotlib as mpl        
import matplotlib.pyplot as plt  
import time


# Set font properties for matplotlib
font = {'family' : 'Serif',
        'weight' : 'bold', 
        'size'   : 10}
mpl.rc('font', **font)  # Apply font settings to matplotlib
mpl.rc('font', **font)  # Apply font settings to matplotlib (duplicate line, can be removed)
mpl.rcParams['figure.dpi'] = 600  # Set the resolution of the figure
mpl.rcParams["mathtext.fontset"] = "dejavuserif"  # Set the font for math text

### Read input file names

In [2]:
# Directory for network inp files
dir = pathlib.Path('../../Networks/Linear Network')
# FIle names for network inp files
partial_name = 'Linear_Network_SWMMIN_'
filenames = ['1000m.inp','100m.inp','25m.inp', '10m.inp','ASD.inp']

### Execute and Time each file

In [23]:
execution_times = []
timing_iterations = 5 # Number of times to run the simulation for each network
stp=0       #steps counter
every=10000  #Interval of printing current time

# Running the simulation for each network
for filename in filenames:
    start_time = time.time()
    for iteration in range(timing_iterations):
        file_path = dir.joinpath(partial_name+ filename)
        print(file_path)
        sim = pyswmm.Simulation(inputfile=str(file_path), outputfile=str(file_path).replace('.inp','.out'))
        
        with sim as sim:
            for step in sim:
                if stp%every==0:
                    print('Current Time is >> ',sim.current_time)
                stp+=1
                pass
    execution_times.append(time.time()-start_time)

..\..\Networks\Linear Network\Linear_Network_SWMMIN_1000m.inp
Current Time is >>  2022-05-18 00:00:00
Current Time is >>  2022-05-18 02:46:40
Current Time is >>  2022-05-18 05:33:20
Current Time is >>  2022-05-18 08:20:00
Current Time is >>  2022-05-18 11:06:40
Current Time is >>  2022-05-18 13:53:20
Current Time is >>  2022-05-18 16:40:00
Current Time is >>  2022-05-18 19:26:40
Current Time is >>  2022-05-18 22:13:20
..\..\Networks\Linear Network\Linear_Network_SWMMIN_1000m.inp
Current Time is >>  2022-05-18 01:01:00
Current Time is >>  2022-05-18 03:47:40
Current Time is >>  2022-05-18 06:34:20
Current Time is >>  2022-05-18 09:21:00
Current Time is >>  2022-05-18 12:07:40
Current Time is >>  2022-05-18 14:54:20
Current Time is >>  2022-05-18 17:41:00
Current Time is >>  2022-05-18 20:27:40
Current Time is >>  2022-05-18 23:14:20
..\..\Networks\Linear Network\Linear_Network_SWMMIN_1000m.inp
Current Time is >>  2022-05-18 02:02:00
Current Time is >>  2022-05-18 04:48:40
Current Time i

In [ ]:
# Display average execution times
execution_times = [times/timing_iterations for times in execution_times]

print(execution_times)

[3.5850544929504395, 3.9745386600494386, 9.000878190994262, 24.315723371505737, 104.0931691646576]


## Extract Target Results from the output files

In [4]:
# Initialize empty DataFrames to store pressures and flowrates
pressures = pd.DataFrame()
flowrates = pd.DataFrame()

# Iterate over each filename in the list of filenames
for filename in filenames:
    last = -1  # Initialize the variable to track the last link or node
    file_path = dir.joinpath(partial_name + filename).with_suffix('.out')  # Construct the file path
    print(file_path)  # Print the file path for debugging purposes
    
    # Open the SWMM output file
    with pyswmm.Output(str(file_path)) as output:
        # Iterate over each link in the output
        for link in output.links:
            link_name = link.split('-')  # Split the link name by '-'
            if link_name[0] == 'P1':  # Check if the link starts with 'P1'
                if int(link_name[1]) > last:  # Update the last link if the current link number is greater
                    last = int(link_name[1])
        link_target = 'P1-' + str(last)  # Construct the target link name
        # Store the flow rate series in the flowrates DataFrame
        flowrates[filename.replace('.inp', '')] = output.link_series(link_target, 'Flow_rate').values()
        
        last = -1  # Reset the variable to track the last node
        # Iterate over each node in the output
        for node in output.nodes:
            node_name = node.split('-')  # Split the node name by '-'
            if node_name[0] == '1':  # Check if the node starts with '1'
                if int(node_name[1]) > last:  # Update the last node if the current node number is greater
                    last = int(node_name[1])
        if last == -1:
            node_target = 'DN1'  # Set the target node to 'DN1' if no nodes were found
        else:
            node_target = '1-' + str(last) + '-DN1'  # Construct the target node name
        # Store the depth series in the pressures DataFrame
        pressures[filename.replace('.inp', '')] = output.node_series(node_target, 'DEPTH').values()
        # Extract the time series from the depth series
        plot_time = list(output.node_series(node_target, 'DEPTH').keys())

..\..\Networks\Linear Network\Linear_Network_SWMMIN_1000m.out
..\..\Networks\Linear Network\Linear_Network_SWMMIN_100m.out
..\..\Networks\Linear Network\Linear_Network_SWMMIN_25m.out
..\..\Networks\Linear Network\Linear_Network_SWMMIN_10m.out
..\..\Networks\Linear Network\Linear_Network_SWMMIN_ASD.out


In [5]:
pressures.max()

1000m    28.065231
100m     12.294351
25m       5.991684
10m       6.165328
ASD       6.133092
dtype: float64

In [7]:
plot_time = pd.Series(plot_time)
time_minutes = (plot_time - plot_time[0]).dt.total_seconds() / 60  # Convert to float hours
font = {'family' : 'Serif',
        'weight' : 'bold', 
        'size'   : 14}
mpl.rc('font', **font)

fig,ax=plt.subplots(2,5,sharex=True)
fig.set_figheight(11)
fig.set_figwidth(24)

# Get 5 colors from PuOr colormap
colors = plt.cm.PuOr([0.2,0.3, 0.35, 0.7,0.8])

ax[0,0].plot(time_minutes,flowrates['1000m'],label="1,000 m",c=colors[0])
ax[1,0].plot(time_minutes,pressures[('1000m')],c=colors[0])
ax[0,1].plot(time_minutes,flowrates["100m"],label="100 m",c=colors[1])
ax[1,1].plot(time_minutes,pressures["100m"],c=colors[1])
ax[0,2].plot(time_minutes,flowrates["25m"],label="25 m",c=colors[2])
ax[1,2].plot(time_minutes,pressures["25m"],c=colors[2])
ax[0,3].plot(time_minutes,flowrates["10m"],label="10 m",c=colors[3])
ax[1,3].plot(time_minutes,pressures["10m"],c=colors[3])
ax[0,4].plot(time_minutes,flowrates["ASD"],label="Pachaly et al. (2020)'s AASD",c=colors[4])
ax[1,4].plot(time_minutes,pressures["ASD"],c=colors[4])
ax[0,0].annotate(r"$t_{exec}$ = "+str(round(execution_times[0],2))+ " s", xy=(21,280))
ax[0,1].annotate(r"$t_{exec}$ = "+str(round(execution_times[1],2))+ " s", xy=(21,280))
ax[0,2].annotate(r"$t_{exec}$ = "+str(round(execution_times[2],2))+ " s", xy=(22,280))
ax[0,3].annotate(r"$t_{exec}$ = "+str(round(execution_times[3],2))+ " s", xy=(18,280))
ax[0,4].annotate(r"$t_{exec}$ = "+str(round(execution_times[4],2))+ " s", xy=(18,280))

xlim1=(0,40)
for i in [0,1,2,3,4]:
    ax[1,i].set_ylim(0,15)
    ax[1,i].set_yticks(np.arange(0,15.1,3))
    ax[0,i].set_ylim(0,300)

ax[0, 0].set_title("Original (1,000 m)")
ax[0, 1].set_title("100 m")
ax[0, 2].set_title("25 m")
ax[0, 3].set_title("10 m")
ax[0, 4].set_title("Pachaly et al. (2020)'s AASD")

ax[0,0].set_ylabel("Flow (LPS)")
ax[1,0].set_ylabel("Pressure (m)")

ax[1,0].annotate(str(round(pressures['1000m'].max(),1))+' m', xy=(10,12),xycoords = 'data', xytext = (15,12), arrowprops = dict(arrowstyle="->"))
# fig.legend(title = "$\Delta x$",loc="lower center",frameon=True,ncol=2, fontsize = 12, bbox_to_anchor = (0.5,-0.02,0,0))
plt.setp(ax, xlim=xlim1,xlabel="Time (min)")
plt.savefig("../Figure Files/Figure 3 - Noise Reduction in Linear Network w exec time",dpi=600)
plt.show

<function matplotlib.pyplot.show(close=None, block=None)>

### Optional: Test Inertial Damping Options

In [8]:
keep_filenames = [filename.replace('.inp', '_Keep.inp') for filename in filenames]
ignore_filenames = [filename.replace('.inp', '_Ignore.inp') for filename in filenames]

# Add columns in pressures and flowrates for the keep and ignore results
for filename in keep_filenames:
    pressures[filename.split('_')[-2] + "_Keep"] = np.nan
    flowrates[filename.split('_')[-2] + "_Keep"] = np.nan

for filename in ignore_filenames:
    pressures[filename.split('_')[-2] + "_Ignore"] = np.nan
    flowrates[filename.split('_')[-2] + "_Ignore"] = np.nan


pressures.head()

1000m  100m  25m  10m  ASD  1000m_Keep  100m_Keep  25m_Keep  10m_Keep  \
0  0.000034   0.0  0.0  0.0  0.0         NaN        NaN       NaN       NaN   
1  0.000125   0.0  0.0  0.0  0.0         NaN        NaN       NaN       NaN   
2  0.000277   0.0  0.0  0.0  0.0         NaN        NaN       NaN       NaN   
3  0.000487   0.0  0.0  0.0  0.0         NaN        NaN       NaN       NaN   
4  0.000752   0.0  0.0  0.0  0.0         NaN        NaN       NaN       NaN   

   ASD_Keep  1000m_Ignore  100m_Ignore  25m_Ignore  10m_Ignore  ASD_Ignore  
0       NaN           NaN          NaN         NaN         NaN         NaN  
1       NaN           NaN          NaN         NaN         NaN         NaN  
2       NaN           NaN          NaN         NaN         NaN         NaN  
3       NaN           NaN          NaN         NaN         NaN         NaN  
4       NaN           NaN          NaN         NaN         NaN         NaN

In [10]:
execution_times = []
timing_iterations = 1 # Number of times to run the simulation for each network
stp=0       #steps counter
every=10000  #Interval of printing current time

dir = dir/"Damping Test"

# Running the simulation for each network
for filename in keep_filenames + ignore_filenames:
    start_time = time.time()
    for iteration in range(timing_iterations):
        file_path = dir.joinpath(partial_name+ filename)
        print(file_path)
        sim = pyswmm.Simulation(inputfile=str(file_path), outputfile=str(file_path).replace('.inp','.out'))
        
        with sim as sim:
            for step in sim:
                if stp%every==0:
                    print('Current Time is >> ',sim.current_time)
                stp+=1
                pass
    execution_times.append(time.time()-start_time)

..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_1000m_Keep.inp
Current Time is >>  2022-05-18 00:00:00
Current Time is >>  2022-05-18 02:46:40
Current Time is >>  2022-05-18 05:33:20
Current Time is >>  2022-05-18 08:20:00
Current Time is >>  2022-05-18 11:06:40
Current Time is >>  2022-05-18 13:53:20
Current Time is >>  2022-05-18 16:40:00
Current Time is >>  2022-05-18 19:26:40
Current Time is >>  2022-05-18 22:13:20
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_100m_Keep.inp
Current Time is >>  2022-05-18 01:01:00
Current Time is >>  2022-05-18 03:47:40
Current Time is >>  2022-05-18 06:34:20
Current Time is >>  2022-05-18 09:21:00
Current Time is >>  2022-05-18 12:07:40
Current Time is >>  2022-05-18 14:54:20
Current Time is >>  2022-05-18 17:41:00
Current Time is >>  2022-05-18 20:27:40
Current Time is >>  2022-05-18 23:14:20
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_25m_Keep.inp
Current Time is >>  2022-05-18 02:01:59
Cur

In [11]:
# Iterate over each filename in the list of filenames
for filename in keep_filenames + ignore_filenames:
    last = -1  # Initialize the variable to track the last link or node
    file_path = dir.joinpath(partial_name + filename).with_suffix('.out')  # Construct the file path
    print(file_path)  # Print the file path for debugging purposes
    
    # Open the SWMM output file
    with pyswmm.Output(str(file_path)) as output:
        # Iterate over each link in the output
        for link in output.links:
            link_name = link.split('-')  # Split the link name by '-'
            if link_name[0] == 'P1':  # Check if the link starts with 'P1'
                if int(link_name[1]) > last:  # Update the last link if the current link number is greater
                    last = int(link_name[1])
        link_target = 'P1-' + str(last)  # Construct the target link name
        # Store the flow rate series in the flowrates DataFrame
        flowrates[filename.replace('.inp', '')] = output.link_series(link_target, 'Flow_rate').values()
        
        last = -1  # Reset the variable to track the last node
        # Iterate over each node in the output
        for node in output.nodes:
            node_name = node.split('-')  # Split the node name by '-'
            if node_name[0] == '1':  # Check if the node starts with '1'
                if int(node_name[1]) > last:  # Update the last node if the current node number is greater
                    last = int(node_name[1])
        if last == -1:
            node_target = 'DN1'  # Set the target node to 'DN1' if no nodes were found
        else:
            node_target = '1-' + str(last) + '-DN1'  # Construct the target node name
        # Store the depth series in the pressures DataFrame
        pressures[filename.replace('.inp', '')] = output.node_series(node_target, 'DEPTH').values()
        # Extract the time series from the depth series
        plot_time = list(output.node_series(node_target, 'DEPTH').keys())

..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_1000m_Keep.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_100m_Keep.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_25m_Keep.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_10m_Keep.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_ASD_Keep.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_1000m_Ignore.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_100m_Ignore.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_25m_Ignore.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_10m_Ignore.out
..\..\Networks\Linear Network\Damping Test\Linear_Network_SWMMIN_ASD_Ignore.out


In [ ]:
# Display average execution times
execution_times = [times/timing_iterations for times in execution_times]

print(execution_times)

[3.752297019958496, 4.199071455001831, 12.69970383644104, 28.13794755935669, 139.64420404434205, 3.9151402950286864, 4.417391586303711, 12.760973405838012, 28.0539448261261, 141.37630968093873]


In [15]:
pressures

1000m     100m       25m       10m       ASD  1000m_Keep  100m_Keep  \
0      0.000034  0.00000  0.000000  0.000000  0.000000    0.000034    0.00000   
1      0.000125  0.00000  0.000000  0.000000  0.000000    0.000125    0.00000   
2      0.000277  0.00000  0.000000  0.000000  0.000000    0.000277    0.00000   
3      0.000487  0.00000  0.000000  0.000000  0.000000    0.000487    0.00000   
4      0.000752  0.00000  0.000000  0.000000  0.000000    0.000752    0.00000   
...         ...      ...       ...       ...       ...         ...        ...   
86335  0.028929  0.00003  0.000236  0.015054  0.020975    0.028932    0.00003   
86336  0.028929  0.00003  0.000236  0.015054  0.020961    0.028932    0.00003   
86337  0.028929  0.00003  0.000236  0.015054  0.020952    0.028932    0.00003   
86338  0.028929  0.00003  0.000236  0.015054  0.020946    0.028932    0.00003   
86339  0.028929  0.00003  0.000236  0.015054  0.020945    0.028932    0.00003   

       25m_Keep  10m_Keep  ASD_Keep  1000m_Ignore  100m_Ignore  25m_Ignore  \
0      0.000000  0.000000  0.000000      0.000034      0.00000    0.000000   
1      0.000000  0.000000  0.000000      0.000125      0.00000    0.000000   
2      0.000000  0.000000  0.000000      0.000277      0.00000    0.000000   
3      0.000000  0.000000  0.000000      0.000487      0.00000    0.000000   
4      0.000000  0.000000  0.000000      0.000752      0.00000    0.000000   
...         ...       ...       ...           ...          ...         ...   
86335  0.000236  0.015120  0.021081      0.028934      0.00003    0.000236   
86336  0.000236  0.015121  0.021087      0.028934      0.00003    0.000236   
86337  0.000236  0.015122  0.021092      0.028934      0.00003    0.000236   
86338  0.000236  0.015123  0.021096      0.028934      0.00003    0.000236   
86339  0.000236  0.015124  0.021100      0.028933      0.00003    0.000236   

       10m_Ignore  ASD_Ignore  
0        0.000000    0.000000  
1        0.000000    0.000000  
2        0.000000    0.000000  
3        0.000000    0.000000  
4        0.000000    0.000000  
...           ...         ...  
86335    0.015088    0.021122  
86336    0.015088    0.021127  
86337    0.015089    0.021130  
86338    0.015089    0.021132  
86339    0.015089    0.021133  

[86340 rows x 15 columns]

In [34]:
flowrates

1000m  100m       25m       10m      3.5m  1000m_Keep  100m_Keep  \
0       6.158291   0.0  0.000000  0.000000  0.000000    6.158291        0.0   
1      12.282660   0.0  0.000000  0.000000  0.000000   12.282660        0.0   
2      18.346146   0.0  0.000000  0.000000  0.000000   18.346146        0.0   
3      24.323128   0.0  0.000000  0.000000  0.000000   24.323128        0.0   
4      30.189650   0.0  0.000000  0.000000  0.000000   30.189650        0.0   
...          ...   ...       ...       ...       ...         ...        ...   
86335   0.000000   0.0  0.000019  0.004345 -0.009642    0.000000        0.0   
86336   0.000000   0.0  0.000017  0.004144 -0.010385    0.000000        0.0   
86337   0.000000   0.0  0.000016  0.003932 -0.010687    0.000000        0.0   
86338   0.000000   0.0  0.000014  0.003712 -0.010539    0.000000        0.0   
86339   0.000000   0.0  0.000012  0.003483 -0.009975    0.000000        0.0   

       25m_Keep  10m_Keep  3.5m_Keep  1000m_Ignore  100m_Ignore  25m_Ignore  \
0      0.000000  0.000000   0.000000      6.158763          0.0    0.000000   
1      0.000000  0.000000   0.000000     12.282596          0.0    0.000000   
2      0.000000  0.000000   0.000000     18.344954          0.0    0.000000   
3      0.000000  0.000000   0.000000     24.320435          0.0    0.000000   
4      0.000000  0.000000   0.000000     30.185345          0.0    0.000000   
...         ...       ...        ...           ...          ...         ...   
86335  0.000014 -0.001786  -0.004817      0.000000          0.0   -0.000020   
86336  0.000012 -0.001889  -0.005684      0.000000          0.0   -0.000021   
86337  0.000010 -0.001985  -0.006383      0.000000          0.0   -0.000023   
86338  0.000009 -0.002074  -0.006919      0.000000          0.0   -0.000025   
86339  0.000007 -0.002155  -0.007312      0.000000          0.0   -0.000026   

       10m_Ignore  3.5m_Ignore  
0        0.000000     0.000000  
1        0.000000     0.000000  
2        0.000000     0.000000  
3        0.000000     0.000000  
4        0.000000     0.000000  
...           ...          ...  
86335    0.000225     0.003677  
86336    0.000127     0.005193  
86337    0.000028     0.006429  
86338   -0.000070     0.007328  
86339   -0.000167     0.007902  

[86340 rows x 15 columns]

In [15]:
plot_time = pd.Series(plot_time)
time_minutes = (plot_time - plot_time[0]).dt.total_seconds() / 60  # Convert to float hours
font = {'family' : 'Serif',
        'weight' : 'bold', 
        'size'   : 14}
mpl.rc('font', **font)

fig,ax=plt.subplots(2,5,sharex=True)
fig.set_figheight(11)
fig.set_figwidth(24)

colors = plt.cm.PuOr([0.2,0.3, 0.35, 0.7,0.8])


ax[0,0].plot(time_minutes,flowrates['1000m'],label="1,000 m",c=colors[0], linestyle = '--')
ax[0,0].plot(time_minutes,flowrates['1000m_Keep'],label="1,000 m Keep",c=colors[0])
ax[1,0].plot(time_minutes,pressures[('1000m')],c=colors[0], linestyle = '--')
ax[1,0].plot(time_minutes,pressures[('1000m_Keep')],c=colors[0])
ax[0,1].plot(time_minutes,flowrates["100m"],label="100 m",c=colors[1], linestyle = '--')
ax[0,1].plot(time_minutes,flowrates["100m_Keep"],label="100 m Keep",c=colors[1])
ax[1,1].plot(time_minutes,pressures["100m"],c=colors[1], linestyle = '--')
ax[1,1].plot(time_minutes,pressures["100m_Keep"],c=colors[1])
ax[0,2].plot(time_minutes,flowrates["25m"],label="25 m",c=colors[2], linestyle = '--')
ax[0,2].plot(time_minutes,flowrates["25m_Keep"],label="25 m Keep",c=colors[2])
ax[1,2].plot(time_minutes,pressures["25m"],c=colors[2], linestyle = '--')
ax[1,2].plot(time_minutes,pressures["25m_Keep"],c=colors[2])
ax[0,3].plot(time_minutes,flowrates["10m"],label="10 m",c=colors[3], linestyle = '--')
ax[0,3].plot(time_minutes,flowrates["10m_Keep"],label="10 m Keep",c=colors[3])
ax[1,3].plot(time_minutes,pressures["10m"],c=colors[3], linestyle = '--')
ax[1,3].plot(time_minutes,pressures["10m_Keep"],c=colors[3])
ax[0,4].plot(time_minutes,flowrates["ASD"],label="Pachaly et al. (2020)'s ASD",c=colors[4], linestyle = '--')
ax[0,4].plot(time_minutes,flowrates["ASD_Keep"],label="Pachaly et al. (2020)'s ASD Keep",c=colors[4])
ax[1,4].plot(time_minutes,pressures["ASD"],c=colors[4], linestyle = '--')
ax[1,4].plot(time_minutes,pressures["ASD_Keep"],c=colors[4])

ax[0,0].annotate(r"$t_{exec}$ = "+str(round(execution_times[0],2))+ " s", xy=(21,280))
ax[0,1].annotate(r"$t_{exec}$ = "+str(round(execution_times[1],2))+ " s", xy=(21,280))
ax[0,2].annotate(r"$t_{exec}$ = "+str(round(execution_times[2],2))+ " s", xy=(22,280))
ax[0,3].annotate(r"$t_{exec}$ = "+str(round(execution_times[3],2))+ " s", xy=(18,280))
ax[0,4].annotate(r"$t_{exec}$ = "+str(round(execution_times[4],2))+ " s", xy=(18,280))

xlim1=(0,40)
for i in [0,1,2,3,4]:
    ax[1,i].set_ylim(0,15)
    ax[1,i].set_yticks(np.arange(0,15.1,3))
    ax[0,i].set_ylim(0,300)

ax[0, 0].set_title("Original (1,000 m)")
ax[0, 1].set_title("100 m")
ax[0, 2].set_title("25 m")
ax[0, 3].set_title("10 m")
ax[0, 4].set_title("Pachaly et al. (2020)'s AASD")

ax[0,0].set_ylabel("Flow (LPS)")
ax[1,0].set_ylabel("Pressure (m)")

ax[1,0].annotate("Dampen: "+ str(round(pressures['1000m'].max(),1))+' m\n Keep: '+ str(round(pressures['1000m_Keep'].max(),1))+' m', 
                 xy=(10,12),xycoords = 'data', xytext = (15,12), arrowprops = dict(arrowstyle="->"))# fig.legend(title = "$\Delta x$",loc="lower center",frameon=True,ncol=2, fontsize = 12, bbox_to_anchor = (0.5,-0.02,0,0))
plt.setp(ax, xlim=xlim1,xlabel="Time (min)")
plt.savefig("../Figure Files/Figure S10 - Noise Reduction - Keep Inertial Terms",dpi=600)
plt.show

<function matplotlib.pyplot.show(close=None, block=None)>

In [14]:
plot_time = pd.Series(plot_time)
time_minutes = (plot_time - plot_time[0]).dt.total_seconds() / 60  # Convert to float hours
font = {'family' : 'Serif',
        'weight' : 'bold', 
        'size'   : 14}
mpl.rc('font', **font)

fig,ax=plt.subplots(2,5,sharex=True)
fig.set_figheight(11)
fig.set_figwidth(24)

ax[0,0].plot(time_minutes,flowrates['1000m'],label="1,000 m",c=colors[0], linestyle = '--')
ax[0,0].plot(time_minutes,flowrates['1000m_Ignore'],label="1,000 m Ignore",c=colors[0])
ax[1,0].plot(time_minutes,pressures[('1000m')],c=colors[0], linestyle = '--')
ax[1,0].plot(time_minutes,pressures[('1000m_Ignore')],c=colors[0])
ax[0,1].plot(time_minutes,flowrates["100m"],label="100 m",c=colors[1], linestyle = '--')
ax[0,1].plot(time_minutes,flowrates["100m_Ignore"],label="100 m Ignore",c=colors[1])
ax[1,1].plot(time_minutes,pressures["100m"],c=colors[1], linestyle = '--')
ax[1,1].plot(time_minutes,pressures["100m_Ignore"],c=colors[1])
ax[0,2].plot(time_minutes,flowrates["25m"],label="25 m",c=colors[2], linestyle = '--')
ax[0,2].plot(time_minutes,flowrates["25m_Ignore"],label="25 m Ignore",c=colors[2])
ax[1,2].plot(time_minutes,pressures["25m"],c=colors[2], linestyle = '--')
ax[1,2].plot(time_minutes,pressures["25m_Ignore"],c=colors[2])
ax[0,3].plot(time_minutes,flowrates["10m"],label="10 m",c=colors[3], linestyle = '--')
ax[0,3].plot(time_minutes,flowrates["10m_Ignore"],label="10 m Ignore",c=colors[3])
ax[1,3].plot(time_minutes,pressures["10m"],c=colors[3], linestyle = '--')
ax[1,3].plot(time_minutes,pressures["10m_Ignore"],c=colors[3])
ax[0,4].plot(time_minutes,flowrates["ASD"],label="Pachaly et al. (2020)'s ASD",c=colors[4], linestyle = '--')
ax[0,4].plot(time_minutes,flowrates["ASD_Ignore"],label="Pachaly et al. (2020)'s ASD Ignore",c=colors[4])
ax[1,4].plot(time_minutes,pressures["ASD"],c=colors[4], linestyle = '--')
ax[1,4].plot(time_minutes,pressures["ASD_Ignore"],c=colors[4])

ax[0,0].annotate(r"$t_{exec}$ = "+str(round(execution_times[0],2))+ " s", xy=(21,280))
ax[0,1].annotate(r"$t_{exec}$ = "+str(round(execution_times[1],2))+ " s", xy=(21,280))
ax[0,2].annotate(r"$t_{exec}$ = "+str(round(execution_times[2],2))+ " s", xy=(22,280))
ax[0,3].annotate(r"$t_{exec}$ = "+str(round(execution_times[3],2))+ " s", xy=(18,280))
ax[0,4].annotate(r"$t_{exec}$ = "+str(round(execution_times[4],2))+ " s", xy=(18,280))

xlim1=(0,40)
for i in [0,1,2,3,4]:
    ax[1,i].set_ylim(0,15)
    ax[1,i].set_yticks(np.arange(0,15.1,3))
    ax[0,i].set_ylim(0,300)

ax[0, 0].set_title("Original (1,000 m)")
ax[0, 1].set_title("100 m")
ax[0, 2].set_title("25 m")
ax[0, 3].set_title("10 m")
ax[0, 4].set_title("Pachaly et al. (2020)'s AASD")

ax[0,0].set_ylabel("Flow (LPS)")
ax[1,0].set_ylabel("Pressure (m)")

ax[1,0].annotate("Dampen: " + str(round(pressures['1000m'].max(),1))+' m\n Ignore: '+ str(round(pressures['1000m_Ignore'].max(),1))+' m', 
                 xy=(10,12),xycoords = 'data', xytext = (15,12), arrowprops = dict(arrowstyle="->"))
# fig.legend(title = "$\Delta x$",loc="lower center",frameon=True,ncol=2, fontsize = 12, bbox_to_anchor = (0.5,-0.02,0,0))
plt.setp(ax, xlim=xlim1,xlabel="Time (min)")
plt.savefig("../Figure Files/Figure S11 - Noise Reduction - Ignore Inertial Terms",dpi=600)

plt.show

<function matplotlib.pyplot.show(close=None, block=None)>